# Visualizing Topic clusters

In this notebook, we will see how to visualize the clusters of topics using dendrogram and also see the exact distances with the help of a heatmap. Let's first train a LDA model to get the topics in kaggle's fake news dataset which can be dowloaded from [here](https://www.kaggle.com/mrisdal/fake-news).

In [12]:
from gensim.models.ldamodel import LdaModel
from gensim.corpora import Dictionary, MmCorpus
import pandas as pd
import re
from gensim.parsing.preprocessing import remove_stopwords, strip_punctuation

import numpy as np
from scipy.spatial.distance import pdist, squareform

import plotly.offline as py
import plotly.graph_objs as go
import plotly.figure_factory as FF

py.init_notebook_mode()

# Train Model

We'll preprocess the data before training. You can refer to this [notebook](https://github.com/RaRe-Technologies/gensim/blob/develop/docs/notebooks/lda_training_tips.ipynb) also for tips and suggestions of pre-processing the text data, and how to train LDA model for getting good results.

In [13]:
df_fake = pd.read_csv('fake.csv')
df_fake[['title', 'text', 'language']].head()
df_fake = df_fake.loc[(pd.notnull(df_fake.text)) & (df_fake.language == 'english')]

# remove stopwords and punctuations
def preprocess(row):
    return strip_punctuation(remove_stopwords(row.lower()))
    
df_fake['text'] = df_fake['text'].apply(preprocess)

# Convert data to required input format by LDA
texts = []
for line in df_fake.text:
    lowered = line.lower()
    words = re.findall(r'\w+', lowered, flags = re.UNICODE | re.LOCALE)
    texts.append(words)
# Create a dictionary representation of the documents.
dictionary = Dictionary(texts)

# Filter out words that occur less than 2 documents, or more than 30% of the documents.
dictionary.filter_extremes(no_below=2, no_above=0.4)
# Bag-of-words representation of the documents.
corpus_fake = [dictionary.doc2bow(text) for text in texts]

In [14]:
lda_fake = LdaModel(corpus=corpus_fake, id2word=dictionary, num_topics=35, chunksize=1500, iterations=200, alpha='auto')
lda_fake.save('lda_35')

In [3]:
lda_fake = LdaModel.load('lda_35')

# Basic Dendrogram

Let's first look at the dendrogram only, to understand how the topic clusters are formed and what does the various values in the plot represents.


In [24]:
from __future__ import absolute_import

from collections import OrderedDict

from plotly import exceptions, optional_imports
from plotly.graph_objs import graph_objs

# Optional imports, may be None for users that only use our core functionality.
np = optional_imports.get_module('numpy')
scp = optional_imports.get_module('scipy')
sch = optional_imports.get_module('scipy.cluster.hierarchy')
scs = optional_imports.get_module('scipy.spatial')


def create_dendrogram(X, orientation="bottom", labels=None,
                      colorscale=None, distfun=None,
                      linkagefun=lambda x: sch.linkage(x, 'complete')):
    """
    BETA function that returns a dendrogram Plotly figure object.
    :param (ndarray) X: Matrix of observations as array of arrays
    :param (str) orientation: 'top', 'right', 'bottom', or 'left'
    :param (list) labels: List of axis category labels(observation labels)
    :param (list) colorscale: Optional colorscale for dendrogram tree
    :param (function) distfun: Function to compute the pairwise distance from
                               the observations
    :param (function) linkagefun: Function to compute the linkage matrix from
                                  the pairwise distances
        clusters
    Example 1: Simple bottom oriented dendrogram
    ```
    import plotly.plotly as py
    from plotly.figure_factory import create_dendrogram
    import numpy as np
    X = np.random.rand(10,10)
    dendro = create_dendrogram(X)
    plot_url = py.plot(dendro, filename='simple-dendrogram')
    ```
    Example 2: Dendrogram to put on the left of the heatmap
    ```
    import plotly.plotly as py
    from plotly.figure_factory import create_dendrogram
    import numpy as np
    X = np.random.rand(5,5)
    names = ['Jack', 'Oxana', 'John', 'Chelsea', 'Mark']
    dendro = create_dendrogram(X, orientation='right', labels=names)
    dendro['layout'].update({'width':700, 'height':500})
    py.iplot(dendro, filename='vertical-dendrogram')
    ```
    Example 3: Dendrogram with Pandas
    ```
    import plotly.plotly as py
    from plotly.figure_factory import create_dendrogram
    import numpy as np
    import pandas as pd
    Index= ['A','B','C','D','E','F','G','H','I','J']
    df = pd.DataFrame(abs(np.random.randn(10, 10)), index=Index)
    fig = create_dendrogram(df, labels=Index)
    url = py.plot(fig, filename='pandas-dendrogram')
    ```
    """
    if not scp or not scs or not sch:
        raise ImportError("FigureFactory.create_dendrogram requires scipy, \
                            scipy.spatial and scipy.hierarchy")

    s = X.shape
    if len(s) != 2:
        exceptions.PlotlyError("X should be 2-dimensional array.")

    if distfun is None:
        distfun = scs.distance.pdist

    dendrogram = _Dendrogram(X, orientation, labels, colorscale,
                             distfun=distfun, linkagefun=linkagefun)

    return {'layout': dendrogram.layout,
            'data': dendrogram.data}


class _Dendrogram(object):
    """Refer to FigureFactory.create_dendrogram() for docstring."""

    def __init__(self, X, orientation='bottom', labels=None, colorscale=None,
                 width="100%", height="100%", xaxis='xaxis', yaxis='yaxis',
                 distfun=None,
                 linkagefun=lambda x: sch.linkage(x, 'complete')):
        self.orientation = orientation
        self.labels = labels
        self.xaxis = xaxis
        self.yaxis = yaxis
        self.data = []
        self.leaves = []
        self.sign = {self.xaxis: 1, self.yaxis: 1}
        self.layout = {self.xaxis: {}, self.yaxis: {}}

        if self.orientation in ['left', 'bottom']:
            self.sign[self.xaxis] = 1
        else:
            self.sign[self.xaxis] = -1

        if self.orientation in ['right', 'bottom']:
            self.sign[self.yaxis] = 1
        else:
            self.sign[self.yaxis] = -1

        if distfun is None:
            distfun = scs.distance.pdist

        (dd_traces, xvals, yvals,
            ordered_labels, leaves) = self.get_dendrogram_traces(X, colorscale,
                                                                 distfun,
                                                                 linkagefun)

        self.labels = ordered_labels
        self.leaves = leaves
        yvals_flat = yvals.flatten()
        xvals_flat = xvals.flatten()

        self.zero_vals = []

        for i in range(len(yvals_flat)):
            if yvals_flat[i] == 0.0 and xvals_flat[i] not in self.zero_vals:
                self.zero_vals.append(xvals_flat[i])

        self.zero_vals.sort()

        self.layout = self.set_figure_layout(width, height)
        self.data = graph_objs.Data(dd_traces)

    def get_color_dict(self, colorscale):
        """
        Returns colorscale used for dendrogram tree clusters.
        :param (list) colorscale: Colors to use for the plot in rgb format.
        :rtype (dict): A dict of default colors mapped to the user colorscale.
        """

        # These are the color codes returned for dendrograms
        # We're replacing them with nicer colors
        d = {'r': 'red',
             'g': 'green',
             'b': 'blue',
             'c': 'cyan',
             'm': 'magenta',
             'y': 'yellow',
             'k': 'black',
             'w': 'white'}
        default_colors = OrderedDict(sorted(d.items(), key=lambda t: t[0]))

        if colorscale is None:
            colorscale = [
                'rgb(0,116,217)',  # blue
                'rgb(35,205,205)',  # cyan
                'rgb(61,153,112)',  # green
                'rgb(40,35,35)',  # black
                'rgb(133,20,75)',  # magenta
                'rgb(255,65,54)',  # red
                'rgb(255,255,255)',  # white
                'rgb(255,220,0)']  # yellow

        for i in range(len(default_colors.keys())):
            k = list(default_colors.keys())[i]  # PY3 won't index keys
            if i < len(colorscale):
                default_colors[k] = colorscale[i]

        return default_colors

    def set_axis_layout(self, axis_key):
        """
        Sets and returns default axis object for dendrogram figure.
        :param (str) axis_key: E.g., 'xaxis', 'xaxis1', 'yaxis', yaxis1', etc.
        :rtype (dict): An axis_key dictionary with set parameters.
        """
        axis_defaults = {
                'type': 'linear',
                'ticks': 'outside',
                'mirror': 'allticks',
                'rangemode': 'tozero',
                'showticklabels': True,
                'zeroline': False,
                'showgrid': False,
                'showline': True,
            }

        if len(self.labels) != 0:
            axis_key_labels = self.xaxis
            if self.orientation in ['left', 'right']:
                axis_key_labels = self.yaxis
            if axis_key_labels not in self.layout:
                self.layout[axis_key_labels] = {}
            self.layout[axis_key_labels]['tickvals'] = \
                [zv*self.sign[axis_key] for zv in self.zero_vals]
            self.layout[axis_key_labels]['ticktext'] = self.labels
            self.layout[axis_key_labels]['tickmode'] = 'array'

        self.layout[axis_key].update(axis_defaults)

        return self.layout[axis_key]

    def set_figure_layout(self, width, height):
        """
        Sets and returns default layout object for dendrogram figure.
        """
        self.layout.update({
            'showlegend': False,
            'autosize': False,
            'hovermode': 'closest',
            'width': width,
            'height': height
        })

        self.set_axis_layout(self.xaxis)
        self.set_axis_layout(self.yaxis)

        return self.layout

    def get_dendrogram_traces(self, X, colorscale, distfun, linkagefun):
        """
        Calculates all the elements needed for plotting a dendrogram.
        :param (ndarray) X: Matrix of observations as array of arrays
        :param (list) colorscale: Color scale for dendrogram tree clusters
        :param (function) distfun: Function to compute the pairwise distance
                                   from the observations
        :param (function) linkagefun: Function to compute the linkage matrix
                                      from the pairwise distances
        :rtype (tuple): Contains all the traces in the following order:
            (a) trace_list: List of Plotly trace objects for dendrogram tree
            (b) icoord: All X points of the dendrogram tree as array of arrays
                with length 4
            (c) dcoord: All Y points of the dendrogram tree as array of arrays
                with length 4
            (d) ordered_labels: leaf labels in the order they are going to
                appear on the plot
            (e) P['leaves']: left-to-right traversal of the leaves
        """
        d = distfun(X)
        Z = linkagefun(d)
        print(Z)
        P = sch.dendrogram(Z, orientation=self.orientation,
                           labels=self.labels, no_plot=True)
        print(P)

        icoord = scp.array(P['icoord'])
        dcoord = scp.array(P['dcoord'])
        ordered_labels = scp.array(P['ivl'])
        color_list = scp.array(P['color_list'])
        colors = self.get_color_dict(colorscale)

        trace_list = []

        for i in range(len(icoord)):
            # xs and ys are arrays of 4 points that make up the '∩' shapes
            # of the dendrogram tree
            if self.orientation in ['top', 'bottom']:
                xs = icoord[i]
            else:
                xs = dcoord[i]

            if self.orientation in ['top', 'bottom']:
                ys = dcoord[i]
            else:
                ys = icoord[i]
            color_key = color_list[i]
            trace = graph_objs.Scatter(
                x=np.multiply(self.sign[self.xaxis], xs),
                y=np.multiply(self.sign[self.yaxis], ys),
                mode='lines',
                marker=graph_objs.Marker(color=colors[color_key]),
                text=['Text A', 'Text B', 'Text C', 'Text D'],
                textposition='bottom'
            )

            try:
                x_index = int(self.xaxis[-1])
            except ValueError:
                x_index = ''

            try:
                y_index = int(self.yaxis[-1])
            except ValueError:
                y_index = ''

            trace['xaxis'] = 'x' + x_index
            trace['yaxis'] = 'y' + y_index

            trace_list.append(trace)

        return trace_list, icoord, dcoord, ordered_labels, P['leaves']

In [25]:
from gensim.matutils import jenson_shannon

# get topic distributions
topic_dist = lda_fake.state.get_lambda()

# use jenson shannon distance metric in dendrogram
def js_dist(X):
    return pdist(X, lambda u, v: jenson_shannon(u, v))

# dendro = FF.create_dendrogram(topic_dist, distfun=js_dist, labels=range(1, 36))
dendro = create_dendrogram(topic_dist, distfun=js_dist, labels=range(1, 36))
dendro['layout'].update({'width':800, 'height':500})
py.iplot(dendro)

[[ 31.          33.           0.22496894   2.        ]
 [ 11.          35.           0.25021555   3.        ]
 [  7.          19.           0.25235737   2.        ]
 [ 16.          20.           0.2614125    2.        ]
 [ 13.          25.           0.28631855   2.        ]
 [ 22.          27.           0.31979089   2.        ]
 [  5.          32.           0.32249407   2.        ]
 [  9.          10.           0.32475227   2.        ]
 [ 14.          38.           0.33052668   3.        ]
 [  1.          39.           0.35558421   3.        ]
 [  4.          44.           0.36283375   4.        ]
 [ 42.          43.           0.36483685   5.        ]
 [ 24.          41.           0.36921632   3.        ]
 [  6.          45.           0.38009328   5.        ]
 [ 23.          40.           0.38645779   3.        ]
 [  3.          28.           0.38924505   2.        ]
 [ 36.          37.           0.3894903    5.        ]
 [ 12.          34.           0.39393307   2.        ]
 [  8.    

It first calculates the pairwise distance between all the topics and then joins the topic that are least distant apart. When all the topics are joined, it then starts joining the clusters and continues the process till root of the tree is reached. There are many methods to join clusters and one of the most common is to calculate average pairwise distance between all the pairs of points in two groups. (In the above dendrogram, plotly uses the default `method=’complete’` available in scipy [here](https://docs.scipy.org/doc/scipy/reference/generated/scipy.cluster.hierarchy.linkage.html) to compute the distance between two clusters)

The x-axis or the leaves of hierarchy represent the topics of our LDA model, y-axis is a measure of closeness of either individual topics or their cluster. Essentially, the y-axis level at which the branches merge (relative to the "root" of the tree) is related to their similarity. For ex., topic 25 and 35 are more similar to each other than to topic 11. In addition, topic 2 and 5 are more similar to each other than topic 25 and 35 are to topic 11 as the height on which they merge (0.17) is lower than the merge height of 25/35 to 11 (0.3).

## Dendrogram with a Heatmap

Now lets append the distance matrix of the topics below the dendrogram in form of heatmap after which we would be able to see the exact distances between all pair of topics.

In [17]:
# Initialize figure by creating upper dendrogram
figure = FF.create_dendrogram(topic_dist, orientation='bottom', distfun=js_dist, labels = range(1, 36))
for i in range(len(figure['data'])):
    figure['data'][i]['yaxis'] = 'y2'

In [18]:
# get distance matrix and it's topic annotations
mdiff, annotation = lda_fake.diff(lda_fake, distance="jenson_shannon", normed=False)

# get reordered topic list
dendro_leaves = figure['layout']['xaxis']['ticktext']
dendro_leaves = list(map(int, dendro_leaves-1))

# reorder distance matrix
heat_data = mdiff[dendro_leaves,:]
heat_data = heat_data[:,dendro_leaves]

In [19]:
annotation_html = [["+++ {}<br>--- {}".format(", ".join(int_tokens), 
                                          ", ".join(diff_tokens)) 
                        for (int_tokens, diff_tokens) in row] 
                       for row in annotation]

heatmap = go.Data([
    go.Heatmap(
        z = heat_data,
        colorscale = 'YIGnBu',
        text = annotation_html
    )
])

heatmap[0]['x'] = figure['layout']['xaxis']['tickvals']
heatmap[0]['y'] = figure['layout']['xaxis']['tickvals']

# Add Heatmap Data to Figure
figure['data'].extend(heatmap)

dendro_leaves = [x+1 for x in dendro_leaves]

# Edit Layout
figure['layout'].update({'width':800, 'height':800,
                         'showlegend':False, 'hovermode': 'closest',
                         })

# Edit xaxis
figure['layout']['xaxis'].update({'domain': [.25, 1],
                                  'mirror': False,
                                  'showgrid': False,
                                  'showline': False,
                                  "showticklabels": True, 
                                  "tickmode": "array",
                                  "ticktext" : dendro_leaves,
                                  "tickvals" : figure['layout']['xaxis']['tickvals'],
                                  'zeroline': False,
                                  'ticks':""})
# Edit yaxis
figure['layout']['yaxis'].update({'domain': [0, 0.75],
                                  'mirror': False,
                                  'showgrid': False,
                                  'showline': False,
                                  "showticklabels": True, 
                                  "tickmode": "array",
                                  "ticktext" : dendro_leaves,
                                  "tickvals" : figure['layout']['xaxis']['tickvals'],
                                  'zeroline': False,
                                  'ticks': ""})
# Edit yaxis2
figure['layout'].update({'yaxis2':{'domain':[0.75, 1],
                                   'mirror': False,
                                   'showgrid': False,
                                   'showline': False,
                                   'zeroline': False,
                                   'showticklabels': False,
                                   'ticks':""}})

py.iplot(figure)

Now the distance matrix is reordered to match the topic cluster order of the upper dendrogram leaves. We can see the exact distance measure between any two topics in the z-value and also their intersecting or different terms in the +++/--- annotation.

In [21]:
from gensim.models import LdaModel

import pyLDAvis as ldavis
import pyLDAvis.gensim

ldavis.enable_notebook()
ldavis.gensim.prepare(lda_fake, corpus_fake, dictionary, sort_topics=False)

/Users/parul/.virtualenvs/gensim3/lib/python3.4/site-packages/pyLDAvis/_prepare.py:387: DeprecationWarning:


.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate_ix



PreparedData(topic_coordinates=            Freq  cluster  topics         x         y
topic                                                
0       0.895350        1       1  0.002643  0.033184
1       1.388914        1       2  0.046845 -0.038404
2       1.073000        1       3  0.044234  0.118053
3       1.642067        1       4 -0.176090 -0.036416
4       3.011363        1       5  0.041672 -0.015654
5       3.690228        1       6  0.056061  0.053853
6       1.705832        1       7  0.069606  0.005022
7       5.574508        1       8  0.121335 -0.131973
8       2.268771        1       9 -0.170713 -0.016531
9       2.412481        1      10 -0.130151 -0.038741
10      2.208436        1      11 -0.116661 -0.017821
11      8.389500        1      12  0.147160 -0.056649
12      1.024766        1      13  0.021275  0.046974
13      1.939378        1      14  0.131520 -0.084733
14      2.356065        1      15 -0.104446 -0.076726
15      1.808494        1      16 -0.007705  0.067670
16      3.980063        1      17 -0.008676 -0.074356
17      2.168635        1      18  0.138973 -0.103867
18      1.296183        1      19 -0.191040 -0.079658
19      2.793355        1      20  0.112336 -0.117509
20      3.541301        1      21 -0.149116 -0.089717
21      1.185910        1      22 -0.013094  0.136512
22      3.371015        1      23  0.009067 -0.006859
23      2.180623        1      24  0.002270  0.114284
24      3.313769        1      25  0.045506  0.180683
25      2.340703        1      26  0.124568 -0.088590
26      1.027130        1      27 -0.002455  0.161560
27      3.249263        1      28 -0.003594  0.112383
28      1.210205        1      29 -0.140120 -0.034055
29      0.320669        1      30 -0.098937  0.022429
30      1.019364        1      31 -0.027040  0.042197
31     11.530286        1      32  0.034940 -0.083682
32      5.689268        1      33  0.080617  0.120285
33      7.422604        1      34  0.075364  0.014834
34      0.970501        1      35  0.033844 -0.037983, topic_info=      Category          Freq        Term         Total  loglift  logprob
term                                                                    
21003  Default  22870.000000     clinton  22870.000000  30.0000  30.0000
44755  Default  23826.000000       trump  23826.000000  29.0000  29.0000
28995  Default   8174.000000      russia   8174.000000  28.0000  28.0000
41438  Default  14911.000000     hillary  14911.000000  27.0000  27.0000
27070  Default  10139.000000    election  10139.000000  26.0000  26.0000
18349  Default   4965.000000     russian   4965.000000  25.0000  25.0000
46779  Default   5161.000000         com   5161.000000  24.0000  24.0000
3424   Default   5858.000000         fbi   5858.000000  23.0000  23.0000
27714  Default   9270.000000         war   9270.000000  22.0000  22.0000
4757   Default   4468.000000        vote   4468.000000  21.0000  21.0000
33906  Default   4207.000000      police   4207.000000  20.0000  20.0000
17501  Default   4325.000000      emails   4325.000000  19.0000  19.0000
52371  Default   4734.000000       syria   4734.000000  18.0000  18.0000
11317  Default   2543.000000     nuclear   2543.000000  17.0000  17.0000
33668  Default   2873.000000          al   2873.000000  16.0000  16.0000
2306   Default   3533.000000       water   3533.000000  15.0000  15.0000
6382   Default   2902.000000      voting   2902.000000  14.0000  14.0000
46043  Default   8004.000000           u   8004.000000  13.0000  13.0000
28612  Default   9911.000000       obama   9911.000000  12.0000  12.0000
21385  Default   2000.000000       saudi   2000.000000  11.0000  11.0000
43542  Default   5344.000000    military   5344.000000  10.0000  10.0000
3374   Default  11631.000000       world  11631.000000   9.0000   9.0000
23524  Default   2993.000000      voters   2993.000000   8.0000   8.0000
39492  Default   7403.000000    campaign   7403.000000   7.0000   7.0000
3092   Default   2376.000000       putin   2376.000000   6.00